In [3]:
# -*- coding: utf-8 -*-
"""
Created on Mon Aug  6 13:16:08 2018

@author: kperks
"""
# INITIALIZATION
from neo import Spike2IO
import os
import numpy as np
import scipy.io as sio
import scipy 
import h5py
from scipy import stats
from scipy import signal
import matplotlib.pyplot as plt
import matplotlib.axes as ax
from pathlib import Path
import random
import sys
import pandas as pd
import seaborn as sns
from scipy.stats import spearmanr, ks_2samp 

In [36]:
def get_range_bounds(win_times,trigger):
    start = np.min(np.where(trigger>win_times[0])[0])
    stop= np.max(np.where(trigger<win_times[1])[0])
    trials = list(range(start,stop))
    return trials
    
def TrialEventTimes(trigger,analevent,trial,win):
    t1 = trigger[trial]
    t2 = t1+win
    EventTimes = analevent[np.where((analevent>t1)&(analevent<t2))]-t1
    return(EventTimes)
    
def get_response(trigger_times,data_func,trial_duration,tau):
    response = [data_func(np.linspace(t,t+trial_duration,int(trial_duration/dt))) for t in trigger_times]
    return np.asarray(response)
    """
    Creates a spike density function from a spike train to do continuous analysis with (such as trial correlations)
    """ 
    
def filtered_response(spk_times, tau):
    """
    Creates a function with a gaussian centered at every spike time (the mean) with standard deviation tau
    """
    spk_times = spk_times.reshape((-1, 1))
    norm_factor = tau * np.sqrt(2. * np.pi)
    return lambda t: np.sum(np.exp(-(spk_times - t.reshape((1, -1))) ** 2 / (2 * tau * tau)), 0) / norm_factor
    
def raster(trigger, data, **kwargs):
    ax = plt.gca();
    
    for ith, t in enumerate(trigger):
        inds = np.where((data>t)&(data<t+md.trial_duration[0]))[0]
        trialdata = data[inds]-t
        plt.scatter(trialdata, np.repeat(ith,len(trialdata)), **kwargs);
        
    plt.ylim(.5, len(trigger) + .5);

###########
#functions to estimate optimal bandwidth for spike density:
def CostFunction(y_hist, N, w, dt):
    """
    References
    ----------
    .. [1] H. Shimazaki and S. Shinomoto, "Kernel Bandwidth Optimization in 
           Spike Rate Estimation," in Journal of Computational Neuroscience 
           29(1-2): 171–182, 2010 http://dx.doi.org/10.1007/s10827-009-0180-4
    """
    # build normal smoothing kernel
    yh = fftkernel(y_hist, w / dt)

    # formula for density
    C = np.sum(yh**2) * dt - 2 * np.sum(yh * y_hist) * dt + 2 \
        / (2 * np.pi)**0.5 / w / N
    C = C * N**2

    return C, yh


def fftkernel(x, w):
    """
    References
    ----------
    .. [1] H. Shimazaki and S. Shinomoto, "Kernel Bandwidth Optimization in 
           Spike Rate Estimation," in Journal of Computational Neuroscience 
           29(1-2): 171–182, 2010 http://dx.doi.org/10.1007/s10827-009-0180-4
    """
    L = x.size
    Lmax = L + 3 * w
    n = 2 ** np.ceil(np.log2(Lmax))

    X = np.fft.fft(x, n.astype(np.int))

    f = np.linspace(0, n-1, n) / n
    f = np.concatenate((-f[0: np.int(n / 2 + 1)],
                        f[1: np.int(n / 2 - 1 + 1)][::-1]))

    K = np.exp(-0.5 * (w * 2 * np.pi * f) ** 2)

    y = np.real(np.fft.ifft(X * K, n))

    y = y[0:L]

    return y

def sskernel(x, tin, W):
    """
    Generates a kernel density estimate with globally-optimized bandwidth.
    The optimal bandwidth is obtained as a minimizer of the formula, sum_{i,j}
    \int k(x - x_i) k(x - x_j) dx  -  2 sum_{i~=j} k(x_i - x_j), where k(x) is
    the kernel function.
    Parameters
    ----------
    x : array_like
        The one-dimensional samples drawn from the underlying density
    tin : array_like
        The values where the density estimate is to be evaluated in generating
        the output 'y'.
    W : array_like
        The kernel bandwidths to use in optimization. Should not be chosen
        smaller than the sampling resolution of 'x'.
    nbs : int, optional
        The number of bootstrap samples to use in estimating the [0.05, 0.95]
        confidence interval of the output 'y'
    Returns
    -------
    y : array_like
        The estimated density, evaluated at points t / tin.
    t : array_like
        The points where the density estimate 'y' is evaluated.
    optw : double
        The optimal global kernel bandwidth.
    C : array_like
        The cost functions associated with the bandwidths 'W'.

    References
    ----------
    .. [1] H. Shimazaki and S. Shinomoto, "Kernel Bandwidth Optimization in 
           Spike Rate Estimation," in Journal of Computational Neuroscience 
           29(1-2): 171–182, 2010 http://dx.doi.org/10.1007/s10827-009-0180-4
    """

    # set argument 't' if not provided
    #always provide xtime input so that output is aligned to trial duration
    T = np.max(x) - np.min(x)
    x_ab = x[(x >= np.min(tin)) & (x <= np.max(tin))]
    dx = np.sort(np.diff(np.sort(x)))
    dt_samp = dx[np.nonzero(dx)][0]
    if dt_samp > np.min(np.diff(tin)):
        t = np.linspace(np.min(tin), np.max(tin), np.min([int(np.ceil(T / dt_samp)), int(1e3)]))
    else:
        t = tin

    # calculate delta t
    dt = min(np.diff(t))

    # create the finest histogram
    thist = np.concatenate((t, (t[-1]+dt)[np.newaxis]))
    y_hist = np.histogram(x_ab, thist-dt/2)[0]
    N = sum(y_hist).astype(np.float)
    y_hist = y_hist / N / dt

    # always provide W
    C = np.zeros((1, len(W)))[0]
    C_min = np.Inf
    ymat=[]
    for k, w in enumerate(W):
        C[k], yh = CostFunction(y_hist, N, w, dt)
        ymat.append(yh)
        if((C[k] < C_min).any()):
            C_min = C[k]
            optw = w
            y = yh
    ymat = np.asarray(ymat)       
    
    return y, t, optw, C, C_min

def get_spikes_kde(trigger_times,data_times,trigger,trial_duration):
    aligned_times = []
    for t in trigger_times:
        thesetimes = data_times[
          np.where((data_times>(trigger[t]))&(data_times<(trigger[t]+trial_duration)))[0]
          ]-(trigger[t])
        aligned_times = np.concatenate((aligned_times,thesetimes)) 

    return np.asarray(aligned_times)

def get_optw(these_trials,spikes,xtime,trigger,trial_duration):
    W=np.arange(0.006,0.2,0.002)
    aligned_times = get_spikes_kde(these_trials,spikes,trigger,trial_duration)
    y, t, optw, C, C_min = sskernel(aligned_times, xtime, W)
    
    return y, t, optw, C, C_min

In [48]:
meta = pd.read_csv('MetaData.csv')

What are the summary statistics for the trial duration in paired experiments? (for Methods section)

In [58]:
meta[((meta['trigger_type']=='paired')
      &(meta['phase']=='phase1')
      &((meta['condition']=='aen_vent') 
        | (meta['condition']=='aen_proprio') 
       |(meta['condition']=='aff_proprio')))].trial_duration.describe()

count    33.000000
mean      2.757576
std       1.565603
min       1.000000
25%       1.500000
50%       2.000000
75%       4.000000
max       6.000000
Name: trial_duration, dtype: float64

In [47]:
######MAIN##########

meta = pd.read_csv('MetaData.csv')

for iexpt,thisexpt_name in enumerate(meta.exptname):
    dt = 1/1000 
    ntrials_per_period = 75 #results did not depend on choice of 50, 75, or 100

    print(iexpt,thisexpt_name)

    thisexpt = meta.loc[meta['exptname'] == thisexpt_name]

    trial_duration = thisexpt.trial_duration.values[0]

    basename = thisexpt_name[0:-8]
    data_folder = Path.cwd() / basename
    file_to_open = data_folder / Path(basename + '.smr')
    bl = Spike2IO(file_to_open,try_signal_grouping=False).read_block()

    trigger = []
    for sublist in np.asarray([seg.events[[s.name for 
       s in seg.events].index(thisexpt.chan_trigger.values[0])].magnitude 
       for seg in bl.segments]):
        for item in sublist:
            trigger.append(item)
    trigger = np.asarray(trigger)

    if thisexpt.spike_times_from.values[0] == 'Spyking-Circus':
        spikes = np.load(data_folder / 'spikes.npy')

    if thisexpt.spike_times_from.values[0] == 'Spike2':
        spikes = []
        for sublist in np.asarray([seg.events[[s.name for 
           s in seg.events].index(thisexpt.chan_spikes.values[0])].magnitude 
           for seg in bl.segments]):
            for item in sublist:
                spikes.append(item)
        spikes = np.asarray(spikes)

    postpairing_range = get_range_bounds([thisexpt.post_start.values[0],
                                          thisexpt.post_stop.values[0]],trigger)
    stim_range = get_range_bounds([thisexpt.stim_start.values[0],
                                   thisexpt.stim_stop.values[0]],trigger)
    base_range = get_range_bounds([thisexpt.base_start.values[0],
                                   thisexpt.base_stop.values[0]],trigger)

    if thisexpt_name == '20060812_3066_SPK.mat':
        #removing a few trials in which spike detection was clearly mis-triggered due to movement artifacts
        removeinds = np.arange(360,np.max(postpairing_range)-1,1)
        [postpairing_range.remove(x) for x in removeinds]
        removeinds = [263, 264, 265, 326, 327] 
        [postpairing_range.remove(x) for x in removeinds]

    xtime = np.linspace(0,trial_duration,trial_duration/dt)

    iei = [(TrialEventTimes(trigger,trigger,trial,10))[0] if len(TrialEventTimes(trigger,trigger,trial,10))>0 else 0 for trial in list(range(0,len(trigger)-1))]

    these_trials = base_range
    y, t, optw, C, C_min= get_optw(these_trials,spikes,xtime,trigger,trial_duration)

    data_func = filtered_response(spikes, optw)

    baseline_r = get_response(trigger[these_trials],data_func,trial_duration,optw)
    baseline_mean = np.mean(baseline_r,0)

    n_trials = len(base_range)
    base_spkrt = [np.shape(np.where((spikes>(trigger[t]))&(spikes<(trigger[t]+trial_duration)))[0])[0]
                  /trial_duration for t in base_range]

    spikemat_base = [spikes[np.where((spikes>trigger[t])&
                    (spikes<trigger[t]+trial_duration))[0]
                    ]-(trigger[t]) for t in base_range]

    if thisexpt_name == '20071025_3335_control_SPK.mat': 
    #not enough baseline recorded so get estimate of baseline from test cell clock trigger baseline
        print('using pre pairing expt to get baseline (recovery end)')
        suppname = '20071025_3335_SPK.mat'
        suppexpt = meta.loc[meta['exptname'] == suppname]
        basename = suppname[0:-8]
        data_folder = Path.cwd() / basename
        supptrigger = np.arange(suppexpt.post_stop.values[0]-250,suppexpt.post_stop.values[0],trial_duration)
        suppbase_range = np.arange(0,len(supptrigger),1)
        base_range = suppbase_range

        suppspikes = np.load(data_folder / 'spikes.npy')

        these_trials = suppbase_range
        y, t, optw, C, C_min= get_optw(these_trials,suppspikes,xtime,supptrigger,trial_duration)

        data_func = filtered_response(suppspikes, optw)

        baseline_mean = np.mean(get_response(
            supptrigger[these_trials],data_func,trial_duration,optw),0)

        base_spkrt = [np.shape(np.where((suppspikes>(supptrigger[t]))&
                                        (suppspikes<(supptrigger[t]+trial_duration)))[0])[0]
                      /trial_duration for t in suppbase_range]
        spikemat_base = [suppspikes[np.where((suppspikes>supptrigger[t])&
                (suppspikes<supptrigger[t]+trial_duration))[0]
                ]-(supptrigger[t]) for t in suppbase_range]


    if thisexpt_name == '20071026_3108_control_SPK.mat': 
    #not enough baseline recorded so get estimate of baseline from test cell clock trigger baseline
        print('using pre pairing expt to get baseline')
        suppname = '20071026_3108_SPK.mat'
        suppexpt = meta.loc[meta['exptname'] == suppname]
        basename = suppname[0:-8]
        data_folder = Path.cwd() / basename
        file_to_open = data_folder / Path(basename + '.smr')
        bl = Spike2IO(file_to_open,try_signal_grouping=False).read_block()
        supptrigger = np.arange(0,suppexpt.base_stop.values[0],trial_duration)
        suppbase_range = np.arange(0,len(supptrigger),1)
        base_range = suppbase_range

        suppspikes = []
        for sublist in np.asarray([seg.events[[s.name for 
           s in seg.events].index(suppexpt.chan_spikes.values[0])].magnitude 
           for seg in bl.segments]):
            for item in sublist:
                suppspikes.append(item)
        suppspikes = np.asarray(suppspikes)

        these_trials = suppbase_range
        y, t, optw, C, C_min= get_optw(these_trials,suppspikes,xtime,supptrigger,trial_duration)

        data_func = filtered_response(suppspikes, optw)

        baseline_mean = np.mean(get_response(
            supptrigger[these_trials],data_func,trial_duration,optw),0)

        base_spkrt = [np.shape(np.where((suppspikes>(supptrigger[t]))&
                                        (suppspikes<(supptrigger[t]+trial_duration)))[0])[0]
                      /trial_duration for t in suppbase_range]
        spikemat_base = [suppspikes[np.where((suppspikes>supptrigger[t])&
                (suppspikes<supptrigger[t]+trial_duration))[0]
                ]-(supptrigger[t]) for t in suppbase_range]

    data_func = filtered_response(spikes, optw)

    npair = len(stim_range)
    ntrials = np.min([npair,ntrials_per_period*2])
    stiminitial_trials = stim_range[0:int(ntrials/2)]
    these_trials = stiminitial_trials
    stimi_spkrt = [np.shape(np.where((spikes>(trigger[t]))&(spikes<(trigger[t]+trial_duration)))[0])[0]
                   /trial_duration for t in these_trials]
    y, t, optw_stim, C, C_min= get_optw(these_trials,spikes,xtime,trigger,trial_duration)
    stiminitial_r = get_response(trigger[these_trials],data_func,trial_duration,optw)
    stiminitial_response = np.mean(stiminitial_r,0)

    stimfinal_trials = stim_range[-int(ntrials/2):]
    these_trials = stimfinal_trials
    stimf_spkrt = [np.shape(np.where((spikes>(trigger[t]))&(spikes<(trigger[t]+trial_duration)))[0])[0]
                   /trial_duration for t in these_trials]
    stimfinal_r = get_response(trigger[these_trials],data_func,trial_duration,optw)
    stimfinal_response = np.mean(stimfinal_r,0)

    npost = len(postpairing_range)
    ntrials = np.min([npost,ntrials_per_period])
    postpairing_trials = postpairing_range[0:ntrials]
    these_trials = postpairing_trials
    post_spkrt = [np.shape(np.where((spikes>(trigger[t]))&(spikes<(trigger[t]+trial_duration)))[0])[0]
                  /trial_duration for t in these_trials]
    postpairing_r = get_response(trigger[these_trials],data_func,trial_duration,optw)
    postpairing_response = np.mean(postpairing_r,0)

    recovery_spkrt = np.nan
    recovery_response = np.full_like(np.empty(len(baseline_mean)),np.nan)
    recovery_trials = [np.nan]
    if npost>=(300+ntrials_per_period):
        recovery_trials = postpairing_range[300:300+ntrials_per_period]
        recovery_spkrt = [np.shape(np.where((spikes>(trigger[t]))&(spikes<(trigger[t]+trial_duration)))[0])[0]
                          /trial_duration for t in recovery_trials]
        these_trials = recovery_trials
        recovery_r = get_response(trigger[these_trials],data_func,trial_duration,optw)
        recovery_response = np.mean(recovery_r,0)


    spikemat_stim = [spikes[np.where((spikes>trigger[t])&
                    (spikes<trigger[t]+trial_duration))[0]
                    ]-(trigger[t]) for t in stim_range]
    spikemat_post = [spikes[np.where((spikes>trigger[t])&
                    (spikes<trigger[t]+trial_duration))[0]
                    ]-(trigger[t]) for t in postpairing_range]

    ccpost = scipy.signal.correlate(postpairing_response,stiminitial_response,mode='same')/(np.var(postpairing_r)*np.var(stiminitial_r))/len(stiminitial_response)
    lags = np.linspace(-(0.5*len(postpairing_response)*dt),(0.5*len(postpairing_response)*dt),len(ccpost))

    datamat = pd.DataFrame({'exptname' : thisexpt_name,
                  'ntrials_base' : [len(base_range)],
                  'ntrials_per_period' : [ntrials_per_period],
                  'ntrials_post' : [len(postpairing_trials)],
                  'ntrials_post_total' : [len(postpairing_range)],
                  'ntrials_recovery' : [len(recovery_trials)],
                  'ntrials_pairing' : [len(stim_range)],
                  'iei_median' : [np.median(iei)],
                  'spkrt_base' : [np.mean(base_spkrt)],
                  'spkrt_stimi' : [np.mean(stimi_spkrt)],
                  'spkrt_stimf' : [np.mean(stimf_spkrt)],
                  'spkrt_post' : [np.mean(post_spkrt)],
                  'spkrt_recovery' : [np.mean(recovery_spkrt)],
                  'latency_minpost' : [xtime[np.where(postpairing_response==np.min(postpairing_response))][0]],
                  'latency_maxstim' : [xtime[np.where(stiminitial_response==np.max(stiminitial_response))][0]],
                  'sp_poststim_mean' : [stats.spearmanr(postpairing_response,stiminitial_response,nan_policy='propagate')[0]],
                  'sp_recoverstim_mean' : [stats.spearmanr(recovery_response,stiminitial_response,nan_policy='propagate')[0]],
                  'sp_basestim_mean' : [stats.spearmanr(baseline_mean,stiminitial_response,nan_policy='propagate')[0]],
                  'ccneg' : [np.min(ccpost)],
                  'ccneg_lag' : [(dt*(np.argmin(ccpost)-len(postpairing_response)))],
                  'ccpos' : [np.max(ccpost)],
                  'ccpos_lag' : [(dt*(np.argmax(ccpost)-len(postpairing_response)))],
                  'cell' : thisexpt.cell.values[0],
                  'condition' : thisexpt.condition.values[0],
                  'trigger_type' : thisexpt.trigger_type.values[0],
                  'phase' : thisexpt.phase.values[0],
                  'optw' : optw,
                  'optw_stim' : optw_stim,
                  'control' : thisexpt.control.values[0]
                    })

    path_to_file = Path.cwd()
    file_to_open = path_to_file / 'DataMat.csv'
    f = open(file_to_open)
    dfimport = pd.read_csv(f.name)
    dfimport = dfimport.loc[:, ~dfimport.columns.str.contains('^Unnamed')]

    dfimport = dfimport.append(datamat,sort=True)
    dfimport = dfimport.drop_duplicates('exptname','last')
    dfimport.to_csv(f.name)

0 20050727_3224_SPK.mat


/anaconda3/lib/python3.6/site-packages/neo-0.8.0.dev0-py3.6.egg/neo/rawio/spike2rawio.py:609: RuntimeWarning: overflow encountered in short_scalars
  info['time_per_adc']) * 1e-6
/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:61: DeprecationWarning: object of type <class 'numpy.float64'> cannot be safely interpreted as an integer.
/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:96: DeprecationWarning: object of type <class 'numpy.float64'> cannot be safely interpreted as an integer.


1 20050728_3404_latency1_SPK.mat
2 20050728_3404_latency2_SPK.mat
3 20050808_3629_latency1_SPK.mat
4 20050808_3629_latency2_SPK.mat
5 20050811_3221_SPK.mat
6 20050818_2874_SPK.mat
7 20050819_2601_SPK.mat
8 20050820_2960_trial1_SPK.mat
9 20050824_2627_control_SPK.mat
10 20050824_2627_trial1_SPK.mat
11 20060626_2815_SPK.mat
12 20060627_2673_SPK.mat
13 20060708_3004_SPK.mat
14 20060710_2767_SPK.mat
15 20060710_3196_SPK.mat
16 20060804_2107_SPK.mat
17 20060812_2921_SPK.mat
18 20060812_3066_SPK.mat
19 20060812_3205_SPK.mat
20 20060816_3893_SPK.mat
21 20070718_598_coupled_SPK.mat
22 20070719_91_coupled_SPK.mat
23 20070720_3352_SPK.mat
24 20070723_287_SPK.mat
25 20070723_311_SPK.mat
26 20070723_339_SPK.mat
27 20070723_415_SPK.mat
28 20070727_3798_SPK.mat
29 20070727_3798_control_SPK.mat
30 20070816_3375_SPK.mat
31 20070816_3509_SPK.mat
32 20071025_3335_SPK.mat
33 20071025_3335_control_SPK.mat
using pre pairing expt to get baseline (recovery end)
34 20071026_3108_SPK.mat
35 20071026_3108_contr